In [4]:
    import fiona
    import os,os.path
    from shapely.geometry import shape,mapping
    from shapely.ops import transform
    from functools import partial
    import pyproj
    from fiona.crs import from_epsg
    import osmnx as ox
    import matplotlib.pyplot as plt
    import geopandas as gpd
    import glob
    import json
    import numpy as np
    import requests as rq
    import collections
    import logging
    import time
    import dateutil.parser
    %matplotlib inline

In [5]:
# Create a custom logger
logger = logging.getLogger(__name__)

# Create handlers
f_handler = logging.FileHandler('Mapillary.log')
f_handler.setLevel(logging.DEBUG)

# Create formatters and add it to handlers
f_format = logging.Formatter('%(asctime)s - %(name)s - %(levelname)s - %(message)s')
f_handler.setFormatter(f_format)

# Add handlers to the logger
logger.addHandler(f_handler)

In [6]:
mapillary_Image_ID = 'https://a.mapillary.com/v3/images?client_id=OFFJd0ZNdzdWY0lkVVpyc2kyZThBZzpkYmIzYTVkYTgxMDBmYmY0&closeto='
distanceFrag = '&radius=200'
mapillary_Image_url = 'https://images.mapillary.com/' #<image_key>/thumb-640.jpg

In [7]:
city = '../Data/GreaterLondon/'
files= glob.glob(city + '*.json')

In [8]:
data = json.load(open(files[1] , 'rb'))

In [9]:
data

{u'51.3171997_-0.1407138': [],
 u'51.3245116452_-0.115121888576': [{u'lat': 51.32443906494612,
   u'lon': -0.1150429207894142,
   u'month': 9,
   u'panoid': u'6PvrSshu5NVo8my4AUKKMw',
   u'year': 2008},
  {u'lat': 51.32441014397448,
   u'lon': -0.1150200015187176,
   u'month': 8,
   u'panoid': u'KxSTO7d0eIvlOGv5ituVOg',
   u'year': 2012},
  {u'lat': 51.32443908953885,
   u'lon': -0.115044888968929,
   u'month': 4,
   u'panoid': u'0yxFMf0i7Dpk4uWxE_hHJw',
   u'year': 2018},
  {u'lat': 51.32436207309369,
   u'lon': -0.1149896603518833,
   u'panoid': u'VzPCo_ijD5BuGBAtvVNheA'},
  {u'lat': 51.32451770228129,
   u'lon': -0.1150999617442986,
   u'panoid': u'7d-rmnc1AoZtAlpvpETwFg'},
  {u'lat': 51.32476091582201,
   u'lon': -0.115264410148133,
   u'panoid': u'4acUgODWCv-hvkk8iDSqpg'},
  {u'lat': 51.32484128170042,
   u'lon': -0.1153196333971973,
   u'panoid': u'B3ogNArUcoaJnpns3hVcCQ'},
  {u'lat': 51.32459841047343,
   u'lon': -0.1151558920897834,
   u'panoid': u'KmYenoddMGRRZvqrvUq53A'},
  {

In [ ]:
for f in files:
    name = 'Mapillary_'+'_'.join(f.split('/')[-1].split('_')[-2:])
    logger.debug("Working with %s"%(f))
    first = json.load(open(f , 'rb'))
    points = []
    for k in first:
        comps = k.split('_')
        point = (comps[1].strip(),comps[0].strip())
        points.append(point)
    logger.debug('Found %d points in this file'%(len(points)))
    
    imagesMeta = []
    for point in points:
        loc= point[0]+','+point[1]
        finalUrl = mapillary_Image_ID + loc + distanceFrag
        try:
            response = rq.get(finalUrl,timeout=5)
            if response.status_code == 200:
                dictionary = json.loads(response.content)
                imagesMeta += dictionary["features"]
            else:
                logger.error('Missed point at (%s,%s)'%(point[0],point[1]))
                time.sleep(10)
        except:
            logger.error('Request Timed out')
    logger.debug('Found %d Images in this file'%(len(imagesMeta)))
    logger.debug('Dumping in file: %s'%(name))
    json.dump(imagesMeta,open(city+name,'wb'))